# **End-to-End Reinforcement Learning with Human Feedback: Reward Modeling and PPO Training**

In [1]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive



## **Load Libraries and configuration of the models**


In [3]:
import torch
from transformers import AutoTokenizer, AutoModelForCausalLM, AutoModelForSequenceClassification, get_linear_schedule_with_warmup, pipeline
from trl import (
    AutoModelForCausalLMWithValueHead, PPOConfig, PPOTrainer,
    RewardConfig, RewardTrainer, setup_chat_format, ModelConfig
)
from datasets import load_dataset
from sklearn.metrics import accuracy_score

In [4]:
# Set model name and device (use GPU if available)
model_name = "gpt2"  # Base model name
# Use CUDA if available, otherwise use CPU
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

# Initialize model configuration
model_config = ModelConfig(model_name_or_path=model_name)

# Load the tokenizer
tokenizer = AutoTokenizer.from_pretrained(
    model_config.model_name_or_path,
    trust_remote_code=model_config.trust_remote_code,
    use_fast=True
)
# Ensure EOS token is used for padding
tokenizer.pad_token = tokenizer.eos_token

# Load models for different purposes: Classification, Reward, Value, Policy
model = AutoModelForSequenceClassification.from_pretrained(
    model_config.model_name_or_path, num_labels=1, trust_remote_code=model_config.trust_remote_code
)
# Reward model for reinforcement learning
reward_model = AutoModelForSequenceClassification.from_pretrained(model_name, num_labels=1).to(device)
# Value model for estimating state values
value_model = AutoModelForSequenceClassification.from_pretrained(model_name, num_labels=1).to(device)
# Policy model for generating actions
policy_model = AutoModelForCausalLM.from_pretrained(model_name).to(device)
# Reference policy model for comparison
ref_policy_model = AutoModelForCausalLM.from_pretrained(model_name).to(device)

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/26.0 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/665 [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/1.04M [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/456k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.36M [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/548M [00:00<?, ?B/s]

Some weights of GPT2ForSequenceClassification were not initialized from the model checkpoint at gpt2 and are newly initialized: ['score.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
Some weights of GPT2ForSequenceClassification were not initialized from the model checkpoint at gpt2 and are newly initialized: ['score.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
Some weights of GPT2ForSequenceClassification were not initialized from the model checkpoint at gpt2 and are newly initialized: ['score.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


generation_config.json:   0%|          | 0.00/124 [00:00<?, ?B/s]

## **Data Preparation**

In [5]:
# Load the ultrafeedback_binarized dataset from the Hugging Face Hub
dataset = load_dataset("trl-lib/ultrafeedback_binarized")

# Define a function to tokenize and preprocess the dataset
def tokenize_function(examples):
    """
    Tokenizes and preprocesses the input examples.

    Args:
        examples: A dictionary of examples containing the "chosen" key.

    Returns:
        A dictionary containing the tokenized input IDs, attention mask, etc.
    """
    return tokenizer(
        [str(x) for x in examples["chosen"]],
        truncation=True,  # Truncate sequences longer than max_length
        padding="max_length",  # Pad shorter sequences to max_length
        max_length=min(tokenizer.model_max_length, 200),  # Set max sequence length (reduced for CUDA memory)
        return_tensors="pt"  # Return PyTorch tensors
    )

# Apply the tokenize_function to the dataset using the `map` function
tokenized_dataset = dataset.map(
    tokenize_function,  # The function to apply
    batched=True,  # Process examples in batches for efficiency
    num_proc=4,  # Use 4 processes for parallel processing
)

README.md:   0%|          | 0.00/643 [00:00<?, ?B/s]

train-00000-of-00001.parquet:   0%|          | 0.00/131M [00:00<?, ?B/s]

test-00000-of-00001.parquet:   0%|          | 0.00/2.14M [00:00<?, ?B/s]

Generating train split:   0%|          | 0/62135 [00:00<?, ? examples/s]

Generating test split:   0%|          | 0/1000 [00:00<?, ? examples/s]

Map (num_proc=4):   0%|          | 0/62135 [00:00<?, ? examples/s]

Map (num_proc=4):   0%|          | 0/1000 [00:00<?, ? examples/s]

In [ ]:
print(dataset) # Shows the features of the original dataset

DatasetDict({
    train: Dataset({
        features: ['chosen', 'rejected', 'score_chosen', 'score_rejected'],
        num_rows: 62135
    })
    test: Dataset({
        features: ['chosen', 'rejected', 'score_chosen', 'score_rejected'],
        num_rows: 1000
    })
})


In [ ]:
print(tokenized_dataset)  # Shows the features of the tokenized dataset

DatasetDict({
    train: Dataset({
        features: ['chosen', 'rejected', 'score_chosen', 'score_rejected', 'input_ids', 'attention_mask'],
        num_rows: 62135
    })
    test: Dataset({
        features: ['chosen', 'rejected', 'score_chosen', 'score_rejected', 'input_ids', 'attention_mask'],
        num_rows: 1000
    })
})


In [6]:
# Save the tokenizer
tokenizer.save_pretrained("drive/MyDrive/M2 D3S/Math of DL/Project/tokenizer")

('drive/MyDrive/M2 D3S/Math of DL/Project/tokenizer/tokenizer_config.json',
 'drive/MyDrive/M2 D3S/Math of DL/Project/tokenizer/special_tokens_map.json',
 'drive/MyDrive/M2 D3S/Math of DL/Project/tokenizer/vocab.json',
 'drive/MyDrive/M2 D3S/Math of DL/Project/tokenizer/merges.txt',
 'drive/MyDrive/M2 D3S/Math of DL/Project/tokenizer/added_tokens.json',
 'drive/MyDrive/M2 D3S/Math of DL/Project/tokenizer/tokenizer.json')

## **Train the Reward Model**

In [ ]:
# Set up chat format for the tokenizer and model if it's not already configured
if tokenizer.chat_template is None:
    # This ensures the tokenizer and model are compatible for chat-style interactions
    model, tokenizer = setup_chat_format(model, tokenizer)

# Configure training arguments for the reward model using RewardConfig
reward_config = RewardConfig(
    output_dir="drive/MyDrive/M2 D3S/Math of DL/Project",
    per_device_train_batch_size=8,
    num_train_epochs=1,
    logging_steps=25,  # Log training progress every 25 steps
    eval_strategy="steps",  # Evaluation strategy: evaluate every 'eval_steps'
    eval_steps=50,  # Evaluate every 50 steps
    remove_unused_columns=False,
    dataset_num_proc=4,
    report_to="none"  # Disable reporting to external tracking services
)

# Define a function to evaluate the model after the training
def compute_metrics(eval_pred):
    logits, labels = eval_pred
    preds = logits.argmax(axis=-1)
    accuracy = accuracy_score(labels, preds)
    return {"accuracy": accuracy}

# Initialize the RewardTrainer with the configuration, model, tokenizer, and datasets
trainer = RewardTrainer(
    args=reward_config,  # Training arguments
    model=model,  # The model to train
    tokenizer=tokenizer,
    train_dataset=tokenized_dataset["train"],
    eval_dataset=tokenized_dataset['test'],
    compute_metrics=compute_metrics,
)

# Start training the reward model
print("Training the reward model...")
trainer.train()
metrics = trainer.evaluate()

The new embeddings will be initialized from a multivariate normal distribution that has old embeddings' mean and covariance. As described in this article: https://nlp.stanford.edu/~johnhew/vocab-expansion.html. To disable this, use `mean_resizing=False`
<ipython-input-5-d48eab8e7e16>:20: FutureWarning: `tokenizer` is deprecated and removed starting from version 0.15.0 for `RewardTrainer.__init__`. Use `processing_class` instead.
  trainer = RewardTrainer(


Map:   0%|          | 0/62135 [00:00<?, ? examples/s]

Map (num_proc=4):   0%|          | 0/62135 [00:00<?, ? examples/s]

Token indices sequence length is longer than the specified maximum sequence length for this model (1063 > 1024). Running this sequence through the model will result in indexing errors
Token indices sequence length is longer than the specified maximum sequence length for this model (1942 > 1024). Running this sequence through the model will result in indexing errors
Token indices sequence length is longer than the specified maximum sequence length for this model (1096 > 1024). Running this sequence through the model will result in indexing errors
Token indices sequence length is longer than the specified maximum sequence length for this model (2164 > 1024). Running this sequence through the model will result in indexing errors


Filter (num_proc=4):   0%|          | 0/62135 [00:00<?, ? examples/s]

...

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━┓
┃ chosen_text                                   ┃ rejected_text                                ┃ logits           ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━┩
│ <|im_start|>user                              │ <|im_start|>user                             │ [0.4951, 0.5049] │
│ Definition: In this task, you are given a     │ Definition: In this task, you are given a    │                  │
│ summary for US Congressional and California   │ summary for US Congressional and California  │                  │
│ state bill, your task is to generate a Title  │ state bill, your task is to generate a Title │                  │
│ for this bill. The preferred titles are under │ for this bill. The preferred titles are      │                  │
│ forty words and mention the purpose of the    │ under forty words and mention the purpose of │                  │
│ bill.                                         │ the bill.                                    │                  │
│ Input: Intelligent Technologies Initiative    │ Input: Intelligent Technologies Initiative   │                  │
│ Act of 2015  This bill directs the Department │ Act of 2015  This bill directs the           │                  │
│ of Transportation (DOT) to establish an       │ Department of Transportation (DOT) to        │                  │
│ Intelligent Technology Initiative to provide  │ establish an Intelligent Technology          │                  │
│ grants to up to six state and local           │ Initiative to provide grants to up to six    │                  │
│ governments to establish deployment sites for │ state and local governments to establish     │                  │
│ large scale installation and operation of     │ deployment sites for large scale             │                  │
│ intelligent transportation systems (ITS) to   │ installation and operation of intelligent    │                  │
│ improve safety, efficiency, system            │ transportation systems (ITS) to improve      │                  │
│ performance, and return on investment. DOT    │ safety, efficiency, system performance, and  │                  │
│ shall develop criteria for selecting grant    │ return on investment. DOT shall develop      │                  │
│ recipients, including how the deployment of   │ criteria for selecting grant recipients,     │                  │
│ technology will enable the recipient to:      │ including how the deployment of technology   │                  │
│ reduce costs and improve return on            │ will enable the recipient to:   reduce costs │                  │
│ investments;   deliver environmental benefits │ and improve return on investments;   deliver │                  │
│ and reduce energy consumption by alleviating  │ environmental benefits and reduce energy     │                  │
│ congestion and streamlining traffic flow;     │ consumption by alleviating congestion and    │                  │
│ measure and improve the operational           │ streamlining traffic flow;   measure and     │                  │
│ performance of its transportation network;    │ improve the operational performance of its   │                  │
│ reduce the number and severity of traffic     │ transportation network;   reduce the number  │                  │
│ collisions and increase driver, passenger,    │ and severity of traffic collisions and       │                  │
│ and pedestrian safety;  collect, disseminate, │ increase driver, passenger, and pedestrian   │                  │
│ and utilize real-time traffic, transit,       │ safety;  collect, disseminate, and utilize   │                  │
│ parking, and other transportation-related     │ real-time traffic, transit, parking, and     │                  │
│ information to improve mobility, reduce       │ other 

/usr/local/lib/python3.10/dist-packages/trl/trainer/utils.py:785: UserWarning: There are 366 out of 550 instances where the predictions for both options are equal. These instances are ignored in the accuracy computation.
  warnings.warn(


┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━┓
┃ chosen_text                                   ┃ rejected_text                                ┃ logits           ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━┩
│ <|im_start|>user                              │ <|im_start|>user                             │ [0.4906, 0.5094] │
│ Definition: In this task, you are given a     │ Definition: In this task, you are given a    │                  │
│ summary for US Congressional and California   │ summary for US Congressional and California  │                  │
│ state bill, your task is to generate a Title  │ state bill, your task is to generate a Title │                  │
│ for this bill. The preferred titles are under │ for this bill. The preferred titles are      │                  │
│ forty words and mention the purpose of the    │ under forty words and mention the purpose of │                  │
│ bill.                                         │ the bill.                                    │                  │
│ Input: Intelligent Technologies Initiative    │ Input: Intelligent Technologies Initiative   │                  │
│ Act of 2015  This bill directs the Department │ Act of 2015  This bill directs the           │                  │
│ of Transportation (DOT) to establish an       │ Department of Transportation (DOT) to        │                  │
│ Intelligent Technology Initiative to provide  │ establish an Intelligent Technology          │                  │
│ grants to up to six state and local           │ Initiative to provide grants to up to six    │                  │
│ governments to establish deployment sites for │ state and local governments to establish     │                  │
│ large scale installation and operation of     │ deployment sites for large scale             │                  │
│ intelligent transportation systems (ITS) to   │ installation and operation of intelligent    │                  │
│ improve safety, efficiency, system            │ transportation systems (ITS) to improve      │                  │
│ performance, and return on investment. DOT    │ safety, efficiency, system performance, and  │                  │
│ shall develop criteria for selecting grant    │ return on investment. DOT shall develop      │                  │
│ recipients, including how the deployment of   │ criteria for selecting grant recipients,     │                  │
│ technology will enable the recipient to:      │ including how the deployment of technology   │                  │
│ reduce costs and improve return on            │ will enable the recipient to:   reduce costs │                  │
│ investments;   deliver environmental benefits │ and improve return on investments;   deliver │                  │
│ and reduce energy consumption by alleviating  │ environmental benefits and reduce energy     │                  │
│ congestion and streamlining traffic flow;     │ consumption by alleviating congestion and    │                  │
│ measure and improve the operational           │ streamlining traffic flow;   measure and     │                  │
│ performance of its transportation network;    │ improve the operational performance of its   │                  │
│ reduce the number and severity of traffic     │ transportation network;   reduce the number  │                  │
│ collisions and increase driver, passenger,    │ and severity of traffic collisions and       │                  │
│ and pedestrian safety;  collect, disseminate, │ increase driver, passenger, and pedestrian   │                  │
│ and utilize real-time traffic, transit,       │ safety;  collect, disseminate, and utilize   │                  │
│ parking, and other transportation-related     │ real-time traffic, transit, parking, and     │                  │
│ information to improve mobility, reduce       │ other 

/usr/local/lib/python3.10/dist-packages/trl/trainer/utils.py:785: UserWarning: There are 355 out of 550 instances where the predictions for both options are equal. These instances are ignored in the accuracy computation.
  warnings.warn(


TrainOutput(global_step=4214, training_loss=0.6972300432618896, metrics={'train_runtime': 8527.7458, 'train_samples_per_second': 3.953, 'train_steps_per_second': 0.494, 'total_flos': 0.0, 'train_loss': 0.6972300432618896, 'epoch': 1.0})

In [ ]:
# Model evaluation
trainer.log_metrics("eval", metrics)

***** eval metrics *****
  eval_accuracy               =     0.7473
  eval_loss                   =     0.6931
  eval_model_preparation_time =     0.0039
  eval_runtime                = 0:00:30.35
  eval_samples_per_second     =     18.121
  eval_steps_per_second       =      2.273


In [ ]:
# Save the model
reward_model.save_pretrained("drive/MyDrive/M2 D3S/Math of DL/Project/reward_model")

**Reward Model Performance**

The reward model achieved the following evaluation results:

- **`eval_loss`**: **0.6931**  
  This represents the cross-entropy loss during evaluation. A lower loss indicates better performance, but the ideal value depends on the specific task and dataset.

- **`eval_accuracy`**: **0.7473**  
  The model correctly classified **74.73%** of the evaluation samples. While this is a good starting point, there's still room for improvement.

- **`eval_runtime`**, **`eval_samples_per_second`**, **`eval_steps_per_second`**  
  These metrics relate to the **efficiency** of the evaluation process and are not directly tied to the model's performance.

---
## Some possible Improvements

- **Increasing the Number of Epochs**: Improves accuracy but comes at the cost of longer training times.
- **Fine-Tuning hyperparameters**: Adjust PPO parameters iteratively while monitoring performance.
- **Augmenting Training Data**: Effective only if the data is relevant, clean, and free of bias.
- **Modifying Reward Functions**: Significantly affects training outcomes and must align with the **downstream application** of your model (e.g., chatbot).


## **Train the Policy Model with PPO**

In [ ]:
# Configure PPO training parameters using PPOConfig
ppo_config = PPOConfig(
    num_train_epochs=1,
    gradient_accumulation_steps=2,
    batch_size=1,
    mini_batch_size=1,  # Mini-batch size for gradient updates within each batch
    learning_rate=1.41e-5, #This lr will be updated through the learning
    output_dir="drive/MyDrive/M2 D3S/Math of DL/Project/PPO_results",
    eval_strategy="steps",  # Evaluate every 'eval_steps'
    eval_steps=50,
    report_to="none"  # Disable reporting to external tracking services
)

# Select 10% of the original training dataset for faster training and apply
# tokenization to the training and evaluation dataset
train_dataset = tokenized_dataset["train"].select(range(int(len(tokenized_dataset["train"]) * 0.1)))
train_dataset = train_dataset.with_format("torch", columns=['input_ids', 'attention_mask'])
eval_dataset = tokenized_dataset["test"].map(tokenize_function, batched=True, num_proc=4)
eval_dataset = eval_dataset.with_format("torch", columns=['input_ids', 'attention_mask'])

# Initialize the PPOTrainer with the configuration, models, and datasets
trainer = PPOTrainer(
    ppo_config,
    reward_model=reward_model,  # Reward model for calculating rewards
    tokenizer=tokenizer,
    policy=policy_model,  # Policy model to be optimized
    ref_policy=ref_policy_model,  # Reference policy model for comparison
    train_dataset=train_dataset,
    eval_dataset=eval_dataset,
    value_model=value_model,  # Value model for estimating state values
)

# Create a learning rate scheduler to optimize the lr
num_update_steps_per_epoch = len(trainer.train_dataset) // ppo_config.gradient_accumulation_steps
num_training_steps = ppo_config.num_train_epochs * num_update_steps_per_epoch

lr_scheduler = get_linear_schedule_with_warmup(
    optimizer=trainer.optimizer,
    num_warmup_steps=0,
    num_training_steps=num_training_steps,
)

# Override the trainer's learning rate scheduler
trainer.lr_scheduler = lr_scheduler

# Start PPO training
trainer.train()

Map (num_proc=4):   0%|          | 0/1000 [00:00<?, ? examples/s]

/usr/local/lib/python3.10/dist-packages/transformers/utils/deprecation.py:165: FutureWarning: `tokenizer` is deprecated and removed starting from version 0.15.0 for `PPOTrainer.__init__`. Use `processing_class` instead.
  return func(*args, **kwargs)
/usr/local/lib/python3.10/dist-packages/transformers/utils/deprecation.py:165: FutureWarning: `policy` is deprecated and removed starting from version 0.15.0 for `PPOTrainer.__init__`. Use `model` instead.
  return func(*args, **kwargs)
/usr/local/lib/python3.10/dist-packages/transformers/utils/deprecation.py:165: FutureWarning: `ref_policy` is deprecated and removed starting from version 0.15.0 for `PPOTrainer.__init__`. Use `ref_model` instead.
  return func(*args, **kwargs)


===training policy===


┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━┓
┃ query                                       ┃ model response                               ┃ score              ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━┩
│ [{'content': 'As an HR manager, you want to │  can't find a word to use in my job.", "What │ 2.5525288581848145 │
│ test a potential employee\'s ability to     │ is the value of x+y = 20 and x-y = 10, what  │                    │
│ solve puzzles to determine their            │ is the value of x and y?", "If a pizza has a │                    │
│ suitability for a job. Write a Python       │ radius of 8 inches and is cut into 6         │                    │
│ script that generates a list of questions   │                                              │                    │
│ that require logical reasoning to answer.   │                                              │                    │
│ Your list should include questions related  │                                              │                    │
│ to mathematical puzzles, language puzzles,  │                                              │                    │
│ logic puzzles, lateral thinking puzzles,    │                                              │                    │
│ and pattern recognition puzzles. Use the    │                                              │                    │
│ following code as a starting                │                                              │                    │
│ point:\nquestions = {\n    "Mathematical    │                                              │                    │
│ puzzles": ["If the value of x+y = 20 and    │                                              │                    │
│ x-y = 10, what is the value of x and y?",   │                                              │                    │
│ "If a pizza has a radius of 8 inches and is │                                              │                    │
│ cut into 6 equal slices, what is the area   │                                              │                    │
│ of each slice?"],\n    "Language puzzles":  │                                              │                    │
│ ["What word starts with \'e\' and ends with │                                              │                    │
│ \'e\' but only contains one letter?", "I am │                                              │                    │
│ taken from a mine, and shut up in a wooden  │                                              │                    │
│ case, from which I                          │                                              │                    │
├─────────────────────────────────────────────┼──────────────────────────────────────────────┼────────────────────┤
│ [{'content': 'Definition: In this task, you │  and pedestrian safety;   improve the safety │ 3.682234048843384  │
│ are given a summary for US Congressional    │ of the public and the environment;   improve │                    │
│ and California state bill, your task is to  │ the quality of life of the public and the    │                    │
│ generate a Title for this bill. The         │ environment;   improve the quality of life   │                    │
│ preferred titles are under forty words and  │ of the public and the environment;   improve │                    │
│ mention the purpose of the bill.\nInput:    │ the quality of life of the                   │                    │
│ Intelligent Technologies Initiative Act of  │                                              │                    │
│ 2015  This bill directs the Department of   │                                              │                    │
│ Transportation (DOT) to establish an        │                                              │                    │
│ Intelligent Technology Initiative to        │         

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━┓
┃ query                                       ┃ model response                               ┃ score              ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━┩
│ [{'content': 'As an HR manager, you want to │  can't read the word. I have to write a      │ 2.732187032699585  │
│ test a potential employee\'s ability to     │ script to solve the problem. I can't read    │                    │
│ solve puzzles to determine their            │ the word. I can't read the word. I can't     │                    │
│ suitability for a job. Write a Python       │ read the word. I can't read the word. I      │                    │
│ script that generates a list of questions   │ can't read the word. I                       │                    │
│ that require logical reasoning to answer.   │                                              │                    │
│ Your list should include questions related  │                                              │                    │
│ to mathematical puzzles, language puzzles,  │                                              │                    │
│ logic puzzles, lateral thinking puzzles,    │                                              │                    │
│ and pattern recognition puzzles. Use the    │                                              │                    │
│ following code as a starting                │                                              │                    │
│ point:\nquestions = {\n    "Mathematical    │                                              │                    │
│ puzzles": ["If the value of x+y = 20 and    │                                              │                    │
│ x-y = 10, what is the value of x and y?",   │                                              │                    │
│ "If a pizza has a radius of 8 inches and is │                                              │                    │
│ cut into 6 equal slices, what is the area   │                                              │                    │
│ of each slice?"],\n    "Language puzzles":  │                                              │                    │
│ ["What word starts with \'e\' and ends with │                                              │                    │
│ \'e\' but only contains one letter?", "I am │                                              │                    │
│ taken from a mine, and shut up in a wooden  │                                              │                    │
│ case, from which I                          │                                              │                    │
├─────────────────────────────────────────────┼──────────────────────────────────────────────┼────────────────────┤
│ [{'content': 'Definition: In this task, you │  and other safety hazards; and   improve the │ 3.37585186958313   │
│ are given a summary for US Congressional    │ safety of the public. The criteria shall     │                    │
│ and California state bill, your task is to  │ include:   the number of miles traveled, the │                    │
│ generate a Title for this bill. The         │ number of vehicles on the road, the number   │                    │
│ preferred titles are under forty words and  │ of vehicles on the road, the number of       │                    │
│ mention the purpose of the bill.\nInput:    │ vehicles on the road, the                    │                    │
│ Intelligent Technologies Initiative Act of  │                                              │                    │
│ 2015  This bill directs the Department of   │                                              │                    │
│ Transportation (DOT) to establish an        │                                              │                    │
│ Intelligent Technology Initiative to        │         

...

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━┓
┃ query                                       ┃ model response                               ┃ score              ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━┩
│ [{'content': 'As an HR manager, you want to │  can't find anything."}                      │ 4.0131754875183105 │
│ test a potential employee\'s ability to     │                                              │                    │
│ solve puzzles to determine their            │ So, that's it. I'm not sure what else I      │                    │
│ suitability for a job. Write a Python       │ should do. I'm not sure what I should do     │                    │
│ script that generates a list of questions   │ with it. I'm not sure what I should do with  │                    │
│ that require logical reasoning to answer.   │ it.                                          │                    │
│ Your list should include questions related  │                                              │                    │
│ to mathematical puzzles, language puzzles,  │ But I'm not sure                             │                    │
│ logic puzzles, lateral thinking puzzles,    │                                              │                    │
│ and pattern recognition puzzles. Use the    │                                              │                    │
│ following code as a starting                │                                              │                    │
│ point:\nquestions = {\n    "Mathematical    │                                              │                    │
│ puzzles": ["If the value of x+y = 20 and    │                                              │                    │
│ x-y = 10, what is the value of x and y?",   │                                              │                    │
│ "If a pizza has a radius of 8 inches and is │                                              │                    │
│ cut into 6 equal slices, what is the area   │                                              │                    │
│ of each slice?"],\n    "Language puzzles":  │                                              │                    │
│ ["What word starts with \'e\' and ends with │                                              │                    │
│ \'e\' but only contains one letter?", "I am │                                              │                    │
│ taken from a mine, and shut up in a wooden  │                                              │                    │
│ case, from which I                          │                                              │                    │
├─────────────────────────────────────────────┼──────────────────────────────────────────────┼────────────────────┤
│ [{'content': 'Definition: In this task, you │  and bicyclist safety;    improve the        │ 3.794977903366089  │
│ are given a summary for US Congressional    │ efficiency of transportation systems; and    │                    │
│ and California state bill, your task is to  │ improve the quality of life of motorists and │                    │
│ generate a Title for this bill. The         │ bicyclists.                                  │                    │
│ preferred titles are under forty words and  │                                              │                    │
│ mention the purpose of the bill.\nInput:    │ The bill also directs DOT to establish a     │                    │
│ Intelligent Technologies Initiative Act of  │ pilot program to evaluate the effectiveness  │                    │
│ 2015  This bill directs the Department of   │ of the technology.                           │                    │
│ Transportation (DOT) to establish an        │                                              │                    │
│ Intelligent Technology Initiative to        │ The     

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━┓
┃ query                                       ┃ model response                               ┃ score              ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━┩
│ [{'content': 'As an HR manager, you want to │  will not speak."]                           │ 3.494645357131958  │
│ test a potential employee\'s ability to     │                                              │                    │
│ solve puzzles to determine their            │ I'm not sure if this is the best way to test │                    │
│ suitability for a job. Write a Python       │ a candidate, but I'm sure it is a good idea. │                    │
│ script that generates a list of questions   │                                              │                    │
│ that require logical reasoning to answer.   │ I'm not sure if this is the best way to test │                    │
│ Your list should include questions related  │ a candidate, but I'm sure                    │                    │
│ to mathematical puzzles, language puzzles,  │                                              │                    │
│ logic puzzles, lateral thinking puzzles,    │                                              │                    │
│ and pattern recognition puzzles. Use the    │                                              │                    │
│ following code as a starting                │                                              │                    │
│ point:\nquestions = {\n    "Mathematical    │                                              │                    │
│ puzzles": ["If the value of x+y = 20 and    │                                              │                    │
│ x-y = 10, what is the value of x and y?",   │                                              │                    │
│ "If a pizza has a radius of 8 inches and is │                                              │                    │
│ cut into 6 equal slices, what is the area   │                                              │                    │
│ of each slice?"],\n    "Language puzzles":  │                                              │                    │
│ ["What word starts with \'e\' and ends with │                                              │                    │
│ \'e\' but only contains one letter?", "I am │                                              │                    │
│ taken from a mine, and shut up in a wooden  │                                              │                    │
│ case, from which I                          │                                              │                    │
├─────────────────────────────────────────────┼──────────────────────────────────────────────┼────────────────────┤
│ [{'content': 'Definition: In this task, you │  and bicyclist safety."}]                    │ 4.3356499671936035 │
│ are given a summary for US Congressional    │                                              │                    │
│ and California state bill, your task is to  │ So, that's it for this post. I'm not sure if │                    │
│ generate a Title for this bill. The         │ this is the best way to do things, but I'm   │                    │
│ preferred titles are under forty words and  │ sure it's a good idea. I'm not sure if this  │                    │
│ mention the purpose of the bill.\nInput:    │ is the only way to                           │                    │
│ Intelligent Technologies Initiative Act of  │                                              │                    │
│ 2015  This bill directs the Department of   │                                              │                    │
│ Transportation (DOT) to establish an        │                                              │                    │
│ Intelligent Technology Initiative to        │         

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━┓
┃ query                                       ┃ model response                               ┃ score              ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━┩
│ [{'content': 'As an HR manager, you want to │  will explain the meaning of the word."}     │ 3.0351994037628174 │
│ test a potential employee\'s ability to     │                                              │                    │
│ solve puzzles to determine their            │ I'm not sure if this is a good idea, but I   │                    │
│ suitability for a job. Write a Python       │ think it's a good idea. I'm not sure if this │                    │
│ script that generates a list of questions   │ is a good idea, but I think it's a good      │                    │
│ that require logical reasoning to answer.   │ idea. I'm                                    │                    │
│ Your list should include questions related  │                                              │                    │
│ to mathematical puzzles, language puzzles,  │                                              │                    │
│ logic puzzles, lateral thinking puzzles,    │                                              │                    │
│ and pattern recognition puzzles. Use the    │                                              │                    │
│ following code as a starting                │                                              │                    │
│ point:\nquestions = {\n    "Mathematical    │                                              │                    │
│ puzzles": ["If the value of x+y = 20 and    │                                              │                    │
│ x-y = 10, what is the value of x and y?",   │                                              │                    │
│ "If a pizza has a radius of 8 inches and is │                                              │                    │
│ cut into 6 equal slices, what is the area   │                                              │                    │
│ of each slice?"],\n    "Language puzzles":  │                                              │                    │
│ ["What word starts with \'e\' and ends with │                                              │                    │
│ \'e\' but only contains one letter?", "I am │                                              │                    │
│ taken from a mine, and shut up in a wooden  │                                              │                    │
│ case, from which I                          │                                              │                    │
├─────────────────────────────────────────────┼──────────────────────────────────────────────┼────────────────────┤
│ [{'content': 'Definition: In this task, you │  and bicyclist safety."}]                    │ 3.1007211208343506 │
│ are given a summary for US Congressional    │                                              │                    │
│ and California state bill, your task is to  │ So, I think that this is a very good idea. I │                    │
│ generate a Title for this bill. The         │ don't know if it's really a good idea, but I │                    │
│ preferred titles are under forty words and  │ think it's a good idea. I think that this is │                    │
│ mention the purpose of the bill.\nInput:    │ a good idea. I think                         │                    │
│ Intelligent Technologies Initiative Act of  │                                              │                    │
│ 2015  This bill directs the Department of   │                                              │                    │
│ Transportation (DOT) to establish an        │                                              │                    │
│ Intelligent Technology Initiative to        │         

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━┓
┃ query                                        ┃ model response                               ┃ score             ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━┩
│ [{'content': 'As an HR manager, you want to  │  can't find a job."}]                        │ 4.367532253265381 │
│ test a potential employee\'s ability to      │                                              │                   │
│ solve puzzles to determine their suitability │ I'm not sure what this is about, but I'm     │                   │
│ for a job. Write a Python script that        │ sure it's a good idea.                       │                   │
│ generates a list of questions that require   │                                              │                   │
│ logical reasoning to answer. Your list       │ I'm not sure if this is a good idea, but I'm │                   │
│ should include questions related to          │ sure it's a good idea.                       │                   │
│ mathematical puzzles, language puzzles,      │                                              │                   │
│ logic puzzles, lateral thinking puzzles, and │                                              │                   │
│ pattern recognition puzzles. Use the         │                                              │                   │
│ following code as a starting                 │                                              │                   │
│ point:\nquestions = {\n    "Mathematical     │                                              │                   │
│ puzzles": ["If the value of x+y = 20 and x-y │                                              │                   │
│ = 10, what is the value of x and y?", "If a  │                                              │                   │
│ pizza has a radius of 8 inches and is cut    │                                              │                   │
│ into 6 equal slices, what is the area of     │                                              │                   │
│ each slice?"],\n    "Language puzzles":      │                                              │                   │
│ ["What word starts with \'e\' and ends with  │                                              │                   │
│ \'e\' but only contains one letter?", "I am  │                                              │                   │
│ taken from a mine, and shut up in a wooden   │                                              │                   │
│ case, from which I                           │                                              │                   │
├──────────────────────────────────────────────┼──────────────────────────────────────────────┼───────────────────┤
│ [{'content': 'Definition: In this task, you  │  and bicyclist safety."]                     │ 4.123383522033691 │
│ are given a summary for US Congressional and │                                              │                   │
│ California state bill, your task is to       │ I'm not sure what this is about. I don't     │                   │
│ generate a Title for this bill. The          │ know. I don't know. I don't know. I don't    │                   │
│ preferred titles are under forty words and   │ know.                                        │                   │
│ mention the purpose of the bill.\nInput:     │                                              │                   │
│ Intelligent Technologies Initiative Act of   │ I don't know. I don't know.                  │                   │
│ 2015  This bill directs the Department of    │                                              │                   │
│ Transportation (DOT) to establish an         │ I don                                        │                   │
│ Intelligent Technology Initiative to provide │        

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━┓
┃ query                                       ┃ model response                               ┃ score              ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━┩
│ [{'content': 'As an HR manager, you want to │  can't find anything else."}                 │ 1.0618345737457275 │
│ test a potential employee\'s ability to     │                                              │                    │
│ solve puzzles to determine their            │ I'm sure you've seen the code before, but    │                    │
│ suitability for a job. Write a Python       │ I'm not sure if it's really there.           │                    │
│ script that generates a list of questions   │                                              │                    │
│ that require logical reasoning to answer.   │ I'm sure you have.                           │                    │
│ Your list should include questions related  │                                              │                    │
│ to mathematical puzzles, language puzzles,  │ I'm sure you have.                           │                    │
│ logic puzzles, lateral thinking puzzles,    │                                              │                    │
│ and pattern recognition puzzles. Use the    │ I'm sure you have                            │                    │
│ following code as a starting                │                                              │                    │
│ point:\nquestions = {\n    "Mathematical    │                                              │                    │
│ puzzles": ["If the value of x+y = 20 and    │                                              │                    │
│ x-y = 10, what is the value of x and y?",   │                                              │                    │
│ "If a pizza has a radius of 8 inches and is │                                              │                    │
│ cut into 6 equal slices, what is the area   │                                              │                    │
│ of each slice?"],\n    "Language puzzles":  │                                              │                    │
│ ["What word starts with \'e\' and ends with │                                              │                    │
│ \'e\' but only contains one letter?", "I am │                                              │                    │
│ taken from a mine, and shut up in a wooden  │                                              │                    │
│ case, from which I                          │                                              │                    │
├─────────────────────────────────────────────┼──────────────────────────────────────────────┼────────────────────┤
│ [{'content': 'Definition: In this task, you │  and bicyclist safety."}                     │ 2.790308713912964  │
│ are given a summary for US Congressional    │                                              │                    │
│ and California state bill, your task is to  │ "The bill also directs DOT to establish a    │                    │
│ generate a Title for this bill. The         │ program to develop a new technology to       │                    │
│ preferred titles are under forty words and  │ improve safety, efficiency, system           │                    │
│ mention the purpose of the bill.\nInput:    │ performance, and return on investment."      │                    │
│ Intelligent Technologies Initiative Act of  │                                              │                    │
│ 2015  This bill directs the Department of   │ "The bill also directs DOT to establish a    │                    │
│ Transportation (DOT) to establish an        │ program to develop a new                     │                    │
│ Intelligent Technology Initiative to        │         

In [ ]:
# Save the optimized PPO model
policy_model.save_pretrained("drive/MyDrive/M2 D3S/Math of DL/Project/ppo_optimized")